## Inter-reader and test-retest stability of foundation model against supervised methods corresponding to Extended Data Figure 3

In [2]:
import pandas as pd
from sklearn.metrics import roc_auc_score
from scipy.special import softmax
import plotly.graph_objects as go
import numpy as np
import pickle
import lifelines
import pingouin as pg
from scipy import stats
from sklearn.metrics import r2_score
import matplotlib.pyplot as plt
import plotly.express as px

## Inter-reader Stability

For the inter-reader variation evaluation, we used the LUNG1 dataset and generated 50 random perturbations sampled from a three-dimensional multivariate normal distribution with zero mean and diagonal covariance matrix for each seed point. Across each dimension, a variance of 16 voxels was used for generating samples. We generated predictions on perturbed seed points using the best foundation and supervised model,  resulting in 50 different prediction models for each

In [3]:
sup_df = pd.read_csv("../outputs/stability/supervised/lung1_input_stability.csv")
foundation_df = pd.read_csv("../outputs/stability/foundation_features/lung1_input_stability.csv")

original = pd.read_csv("../data/preprocessing/lung1/annotations.csv")

In [4]:
def compute_stability_metrics(df):
    trials = 50

    results_df = pd.DataFrame()

    for n_trial in range(trials):
        trial_df = df[df["trial"] == n_trial]

        # For the feature based model, load the model and predict
        pred = np.vstack([trial_df["pred_0"].values, trial_df["pred_1"].values])

        pred = softmax(pred, axis=0)
        auc = roc_auc_score(trial_df["survival"], pred[1])
        ci = lifelines.utils.concordance_index(trial_df["Survival.time"], pred[1], trial_df["deadstatus.event"])

        row = {
            "trial": n_trial,
            "AUC": auc,
            "CI": ci,
            "x": original["coordX"].values - trial_df["coordX"].values,
            "y": original["coordY"].values - trial_df["coordY"].values,
            "z": original["coordZ"].values - trial_df["coordZ"].values,
        }

        results_df = results_df.append(row, ignore_index=True)

    return results_df

In [5]:
sup_df = compute_stability_metrics(sup_df)
foundation_df = compute_stability_metrics(foundation_df)

/tmp/ipykernel_2402816/904856132.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results_df = results_df.append(row, ignore_index=True)
/tmp/ipykernel_2402816/904856132.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results_df = results_df.append(row, ignore_index=True)
/tmp/ipykernel_2402816/904856132.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results_df = results_df.append(row, ignore_index=True)
/tmp/ipykernel_2402816/904856132.py:25: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  results_df = results_df.append(row, ignore_index=True)
/tmp/ipykernel_2402816/904856132.py:25: FutureWarning: The frame.append method i

### Display input perturbations over x and y-axis

In [7]:
x_dist, y_dist, z_dist = [], [], []
for x_list, y_list, z_list in zip(foundation_df["x"], foundation_df["y"], foundation_df["z"]):
    x_dist += list(x_list)
    y_dist += list(y_list)
    z_dist += list(z_list)

In [12]:
df = {"x": x_dist, "y": y_dist, "z": z_dist}
fig = px.density_heatmap(
    df,
    "x",
    "y",
    marginal_x="histogram",
    marginal_y="histogram",
    labels={"x": "x-axis perturbation", "y": "y-axis perturbation"},
    color_continuous_scale=px.colors.sequential.Greens,
)
for trace in fig.data:
    if type(trace) == go.Histogram:
        trace.marker = dict(
            opacity=0.8,
            cauto=True,
        )
        trace.opacity = 1

fig.update_layout(template="plotly_white", width=600, height=600, xaxis=dict(tickmode="linear", tick0=0, dtick=5))

### Plot prognostic stability of the feature extractor foundation model against the fine-tuned supervised model when the input seed point is perturbed, estimated through AUC for 2-year survival. 

In [7]:
sup_df["model"] = "Supervised"
foundation_df["model"] = "Foundation model"

df = pd.concat([foundation_df, sup_df])

In [8]:
for metric in ["CI", "AUC"]:
    colors = ["rgb(115,115,115)", "rgb(189,189,189)", "rgb(49,130,189)", "rgb(0, 163, 213)"]

    fig = px.box(
        df,
        x="model",
        y=metric,
        color="model",
        template="plotly_white",
        width=500,
        height=600,
        points="all",
        color_discrete_sequence=[colors[2], colors[1]],
    )

    min_val = min(np.min(foundation_df[metric]), np.min(sup_df[metric])) - 0.01
    fig.add_annotation(
        x=0,
        y=min_val,
        text=f"μ={np.mean(foundation_df[metric]):.2f}, σ={np.std(foundation_df[metric]):.3f}",
        showarrow=False,
        font=dict(size=10),
    )
    fig.add_annotation(
        x=1,
        y=min_val,
        text=f"μ={np.mean(sup_df[metric]):.2f}, σ={np.std(sup_df[metric]):.3f}",
        showarrow=False,
        font=dict(size=10),
    )

    fig.show()

## Test-Retest stability

In [8]:
def process_rider_preds(df):
    df["ID"] = df["PatientID"].str.split("-").str[0]
    df["tag"] = df["PatientID"].str.split("-").str[1]

    pred = np.vstack([df["pred_0"].values, df["pred_1"].values])

    from scipy.special import softmax

    pred = softmax(pred, axis=0)
    df["pred_0"] = pred[0]
    df["pred_1"] = pred[1]

    df.sort_values(by="ID", inplace=True)

    return df

In [15]:
sup_df = pd.read_csv("../outputs/stability/supervised/rider_test_retest.csv")
foundation_df = pd.read_csv("../outputs/stability/foundation_features/rider_test_retest.csv")

In [16]:
foundation_df = process_rider_preds(foundation_df)
sup_df = process_rider_preds(sup_df)

### Computing ICC

In [20]:
pg.intraclass_corr(data=foundation_df, targets="ID", raters="tag", ratings="pred_1")

Type              Description       ICC           F  df1  df2  \
0   ICC1   Single raters absolute  0.984210  125.659910   25   26   
1   ICC2     Single random raters  0.984214  130.002368   25   25   
2   ICC3      Single fixed raters  0.984733  130.002368   25   25   
3  ICC1k  Average raters absolute  0.992042  125.659910   25   26   
4  ICC2k    Average random raters  0.992044  130.002368   25   25   
5  ICC3k     Average fixed raters  0.992308  130.002368   25   25   

           pval         CI95%  
0  2.547630e-21  [0.97, 0.99]  
1  8.354885e-21  [0.97, 0.99]  
2  8.354885e-21  [0.97, 0.99]  
3  2.547630e-21   [0.98, 1.0]  
4  8.354885e-21   [0.98, 1.0]  
5  8.354885e-21   [0.98, 1.0]

In [13]:
import pingouin as pg
icc = pg.intraclass_corr(data=data, targets='Wine', raters='Judge', ratings='Score')


In [28]:
pg.intraclass_corr(data=foundation_df, targets="ID", raters="tag", ratings="pred_1")

Type              Description       ICC           F  df1  df2  \
0   ICC1   Single raters absolute  0.984210  125.659910   25   26   
1   ICC2     Single random raters  0.984214  130.002368   25   25   
2   ICC3      Single fixed raters  0.984733  130.002368   25   25   
3  ICC1k  Average raters absolute  0.992042  125.659910   25   26   
4  ICC2k    Average random raters  0.992044  130.002368   25   25   
5  ICC3k     Average fixed raters  0.992308  130.002368   25   25   

           pval         CI95%  
0  2.547630e-21  [0.97, 0.99]  
1  8.354885e-21  [0.97, 0.99]  
2  8.354885e-21  [0.97, 0.99]  
3  2.547630e-21   [0.98, 1.0]  
4  8.354885e-21   [0.98, 1.0]  
5  8.354885e-21   [0.98, 1.0]

In [90]:
results_df = pd.DataFrame()
for df, model in zip([sup_df, foundation_df], ["Supervised (Finetuned)", "Foundation (Features)"]):
    res = pg.intraclass_corr(data=df, targets="ID", raters="tag", ratings="pred_1")
    row = {
        "ICC": res.iloc[2, 2],
        "Model": model,
        "CI_low": res.iloc[2, 7][0],
        "CI_high": res.iloc[2, 7][1],
        "p": res.iloc[2, 6]
    }

    results_df = results_df.append(row, ignore_index=True)

/tmp/ipykernel_3246002/402031836.py:12: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

/tmp/ipykernel_3246002/402031836.py:12: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.



In [142]:
import plotly.graph_objects as go

fig = go.Figure()
colors = ["rgb(115,115,115)", "rgb(49,130,189)"][::-1]

for i, model in enumerate(reversed(results_df['Model'].unique())):
    model_df = results_df[results_df['Model'] == model]
    fig.add_trace(go.Bar(
        x=model_df['Model'],
        y=model_df['ICC'],
        name=model,
        marker_color=colors[i],
        error_y=dict(
            type='data',
            symmetric=False,
            array=model_df['CI_high'] - model_df['ICC'],
            arrayminus=model_df['ICC'] - model_df['CI_low']
        )
    ))

fig.update_layout(
    title='ICC with Confidence Intervals for each Model',
    yaxis_title='Intraclass Correlation Coefficient (ICC)',
    template='simple_white',
    width=250,
    legend=dict(
        orientation="h",
        yanchor="bottom",
        y=-0.3,
        xanchor="right",
        x=1
    ),
    bargap=0,
    xaxis=dict(showticklabels=False),
    yaxis=dict(range=[0.8, 1])  # Added this line to reduce the range of y axis
)

fig.write_image("figures/icc.png", scale=10)
fig.show()


### Compute Scatter plot of test vs retest

In [76]:
def process_rider_preds(df, softmax=False):
    df["ID"] = df["PatientID"].str.split("-").str[0]
    df["tag"] = df["PatientID"].str.split("-").str[1]

    if softmax:
        pred = np.vstack([df["pred_0"].values, df["pred_1"].values])

        from scipy.special import softmax

        pred = softmax(pred, axis=0)
        df["pred_0"] = pred[0]
        df["pred_1"] = pred[1]

        test_df = df[df["tag"] == "test"].sort_values(by="ID", ascending=False)["pred_1"]
        retest_df = df[df["tag"] == "retest"].sort_values(by="ID", ascending=False)["pred_1"]

    else:
        test_df = df[df["tag"] == "test"].sort_values(by="ID", ascending=False).filter(like="pred")
        retest_df = df[df["tag"] == "retest"].sort_values(by="ID", ascending=False).filter(like="pred")

    return test_df, retest_df

In [77]:
test, retest = process_rider_preds(sup_df)
r2 = r2_score(test.values.ravel(), retest.values.ravel())
sim = stats.spearmanr(test.values.ravel(), retest.values.ravel())

colors = ["rgb(115,115,115)", "rgb(189,189,189)", "rgb(49,130,189)", "rgb(0, 163, 213)"]

df = pd.DataFrame({"Test": test.values.ravel(), "Retest": retest.values.ravel()})
fig = px.scatter(
    x="Test",
    y="Retest",
    data_frame=df,
    opacity=0.6,
    color_discrete_sequence=[colors[1]],
    trendline_color_override="black",
    title=f"Supervised <br><span style='font-size: 12px;'><i>R<sup>2</sup>{r2:.3f}<br>Spearman corr: {sim.correlation:.3f}</i></span>",
    width=600,
    height=600,
    template="plotly_white",
)
fig.show()


test, retest = process_rider_preds(foundation_df)
r2 = r2_score(test.values.ravel(), retest.values.ravel())
sim = stats.spearmanr(test.values.ravel(), retest.values.ravel())
df = pd.DataFrame({"Test": test.values.ravel(), "Retest": retest.values.ravel()})

fig = px.scatter(
    x="Test",
    y="Retest",
    data_frame=df,
    opacity=0.6,
    color_discrete_sequence=[colors[2]],
    trendline_color_override="black",
    title=f"Foundation model <br><span style='font-size: 12px;'><i>R<sup>2</sup>: {r2:.3f}<br>Spearman corr: {sim.correlation:.3f}</i></span>",
    width=600,
    height=600,
    template="plotly_white",
)
fig.show()

In [111]:
sup_df = pd.read_csv("../outputs/stability/supervised/LUNG1_perturbed_feats.csv")
foundation_df = pd.read_csv("../outputs/stability/foundation_features/LUNG1_perturbed_feats.csv")

original = pd.read_csv("../data/preprocessing/lung1/annotations.csv")

In [133]:
def compute_feature_stability_metrics(df):
    trials = df['trial'].nunique()
    mse_items = []

    ref = df[df["trial"] == 0].filter(like="pred").values
    for n_trial in range(1, trials):
        trial_df = df[df["trial"] == n_trial]
        feats = trial_df.filter(like="pred").values

        mse = np.mean((ref - feats)**2)
        row = {
            "trial": n_trial,
            "MSE": mse
        }

        mse_items.append(row)

    return mse_items


In [ ]:
sup_df = pd.DataFrame(compute_feature_stability_metrics(sup_df))
sup_df["model"] = "Supervised (Finetuned)"
foundation_df = pd.DataFrame(compute_feature_stability_metrics(foundation_df))
foundation_df["model"] = "Foundation (Features)"

In [138]:
df = pd.concat([foundation_df, sup_df])

In [141]:
for metric in ["MSE"]:
    colors = ["rgb(115,115,115)", "rgb(189,189,189)", "rgb(49,130,189)", "rgb(0, 163, 213)"]

    fig = px.box(
        df,
        x="model",
        y=metric,
        color="model",
        template="plotly_white",
        width=500,
        height=600,
        points="all",
        color_discrete_sequence=[colors[2], colors[0]],
    )

    min_val = min(np.min(foundation_df[metric]), np.min(sup_df[metric])) - 0.01
    fig.add_annotation(
        x=0,
        y=min_val,
        text=f"μ={np.mean(foundation_df[metric]):.2f}, σ={np.std(foundation_df[metric]):.3f}",
        showarrow=False,
        font=dict(size=10),
    )
    fig.add_annotation(
        x=1,
        y=min_val,
        text=f"μ={np.mean(sup_df[metric]):.2f}, σ={np.std(sup_df[metric]):.3f}",
        showarrow=False,
        font=dict(size=10),
    )

    fig.write_image("figures/feature_stability.png", scale=10)

    fig.show()